# Plot vertical profiles at one point

Velocity, concentration, density profiles

Like this
1. Use 'makeVerticalSlice' to get a DataArray with proper vertical coordinates according to depth
2. Select a M and N point and a time (or not, then you get a time slider widget)
2. Plot that selection with hvPlot

In [1]:
import xarray as xr
import hvplot.xarray
from JulesD3D.processNetCDF import fixMeshGrid, makeVelocity, addDepth, addVectorSum, makeVerticalSlice
from JulesD3D.utils import ncFilePicker, quickDF, folderPicker, easyTimeFormat
import numpy as np
from os import path
from IPython.display import Markdown as md 
%load_ext autoreload

In [2]:
parent_folder = '/Users/julesblom/ThesisResults/'
# scenario_folder = folderPicker(parent_folder)
# scenario_folder

In [3]:
nc_filename = ncFilePicker(parent_folder) #scenario_folder.value)
nc_filename

Select(description='NetCDF file:', layout=Layout(height='120px', width='100%'), options=('/Users/julesblom/The…

In [4]:
trim = xr.open_dataset(nc_filename.value)

In [5]:
if 'velocity' not in trim:
    trim = fixMeshGrid(trim, mystery_flag=True)
    trim = addDepth(trim) # this is needed for calculating the ylims automatically
    trim = makeVelocity(trim, transpose=False)
else:
    print("DataSet is preprocessed, atleast, 'velocity' is already in DataSet")

● Fixing mesh grid, assuming a uniform grid 
132 x 182 grid


/Users/julesblom/Library/Caches/pypoetry/virtualenvs/delft3d-python-j5EFwY34-py3.7/lib/python3.7/site-packages/xarray/core/computation.py:1215: FutureWarning: This DataArray contains multi-dimensional coordinates. In the future, these coordinates will be transposed as well unless you specify transpose_coords=False.
  return result.transpose(*[d for d in all_dims if d in result.dims])


In [6]:
basename = path.basename(nc_filename.value)
plot_title, _ = path.splitext(basename)
plot_title

'Slope085_Run01'

In [7]:
channel_index = int(trim.M.size/2)
ambient_density = trim.RHOCONST.values

# N coord in cell just behind head for different scenarios
# if '085' in plot_title:
#     N_point = 43 #  behind head; y = 8600
# elif '100' in plot_title:
#     N_point = 45 # behind head; y = 9200
# elif '125' in plot_title:
#     N_point = 50 #  behind head; y = 10200

N_point = 78

md(f"## Check the damn N-coord for {plot_title}: {N_point} ")

## Check the damn N-coord for Slope085_Run01: 78 

In [8]:
trim.XZ.isel(M=channel_index, N=N_point)

<xarray.DataArray 'XZ' ()>
array(13100)
Coordinates:
    XZ       int64 13100
    YZ       int64 15600
Attributes:
    standard_name:  projection_x_coordinate
    long_name:      X-coordinate of cell centres
    units:          m

Like always, extract all settings that are shared among all plots into a single, neat dict

In [14]:
plot_settings = dict(groupby=['time', 'N'],
                     height=400,
                     width=280,
                     grid=True,
                     legend=False,
                     ylabel='Depth (m)'
                    )

In [12]:
lower_depth = int(trim.isel(M=channel_index, N=N_point).depth_center.min().values)
upper_depth = int(lower_depth + 15)
ylims = (lower_depth, upper_depth)
ylims

(-523, -508)

# Density profile

In [35]:
density_slice = makeVerticalSlice(trim, 'RHO').isel(M=channel_index, N=N_point)

max_density = density_slice.max().values
auto_density_lim = (float(ambient_density), float(max_density))
auto_density_lim

(1025.0, 1053.97998046875)

In [36]:
density_vert_profile = density_slice.hvplot.line('RHO', 'depth_center', 
                                        xlim=auto_density_lim,
                                        ylim=ylims,
                                        **plot_settings
                            )

density_vert_profile

:DynamicMap   [time,N]
   :NdOverlay   [N_KMAXOUT_RESTR]
      :Curve   [RHO]   (depth_center)

## Excess density / mass concentration

In [37]:
trim['delta_rho'] = trim.RHO - ambient_density
trim['delta_rho'].dims

('time', 'KMAXOUT_RESTR', 'M', 'N')

In [38]:
excess_density_slice = makeVerticalSlice(trim, 'delta_rho').isel(M=channel_index, N=N_point)

excess_density_vert_profile = excess_density_slice.hvplot.line('delta_rho', 'depth_center', 
                                        xlim=(0, 65),
                                        ylim=ylims,
                                        title="Excess Density Profile",       
                                        xlabel="Density (kg/m3)",
                                        color='#00846b',
                                        **plot_settings
                            )

excess_density_vert_profile

:DynamicMap   [time,N]
   :NdOverlay   [N_KMAXOUT_RESTR]
      :Curve   [delta_rho]   (depth_center)

## Concentration profile

In [39]:
SAND = 0
SILT = 1

In [48]:
concentration_slice = makeVerticalSlice(trim, 'R1')
sand_conc_slice = concentration_slice.isel(LSTSCI=SAND, M=channel_index, N=N_point)
silt_conc_slice = concentration_slice.isel(LSTSCI=SILT, M=channel_index, N=N_point)

In [49]:
silt_conc_vert_profile = silt_conc_slice.hvplot.line('R1', 'depth_center', 
                                        xlim=(0.0, 85),
                                        ylim=ylims,
                                        title="Volume Conc. Profile",
                                        label="Silt",
                                        color="#00204c",
                                        xlabel="Volume concentration (%)",
                                        **plot_settings                                                     
                                    )

In [50]:
sand_conc_vert_profile = sand_conc_slice.hvplot.line('R1', 'depth_center', 
                                        xlim=(0.0, 85),
                                        ylim=ylims,
                                        title="Volume Conc. Profile",
                                        label="Sand",
                                        xlabel="Volume concentration (%)",
                                        color="#c2b36c",
                                        **plot_settings 
                                    )
sand_conc_vert_profile

:DynamicMap   [time,N]
   :NdOverlay   [N_KMAXOUT_RESTR]
      :Curve   [R1]   (depth_center)

In [51]:
sand_conc_vert_profile * silt_conc_vert_profile

:DynamicMap   [time,N]
   :Overlay
      .NdOverlay.Sand :NdOverlay   [N_KMAXOUT_RESTR]
         :Curve   [R1]   (depth_center)
      .NdOverlay.Silt :NdOverlay   [N_KMAXOUT_RESTR]
         :Curve   [R1]   (depth_center)

# Velocity profile

In [52]:
velocity_slice = makeVerticalSlice(trim, 'velocity').isel(M=channel_index, N=N_point)

In [53]:
velocity_vert_profile = velocity_slice.hvplot.line('velocity', 'depth_center', 
                                        xlim=(0, 3.5),
                                        ylim=ylims,
                                        color='tomato',
                                        title='Velocity Profile',
                                        **plot_settings
                                    )

In [56]:
velocity_vert_profile

:DynamicMap   [time,N]
   :NdOverlay   [N_KMAXOUT_RESTR]
      :Curve   [velocity]   (depth_center)

## Turbulent Energy
All wiggly :(

In [18]:
# turbu_energy_slice = makeVerticalSlice(trim, 'RTUR1').isel(M=channel_index, N=N_point, LTUR=0)
# turbu_slice.hvplot.line('RTUR1', 'depth', 
#                                         xlim=(0, 5e-4),
#                                         ylim=ylims,
#                                         color='steelblue',
#                                         **plot_settings
#                                     )

:DynamicMap   [time,N]
   :NdOverlay   [N_KMAXOUT]
      :Curve   [RTUR1]   (depth)

In [61]:
map_settings = {
    'height': 400,
    'width': 344,
    'rasterize': True,
    'dynamic': True,
#     'legend': True,
    'attr_labels': True,    
}

mapview = trim.velocity.isel(KMAXOUT_RESTR=67).hvplot.quadmesh('XZ', 'YZ',                      
                        cmap='inferno',
                        clim=(0, 1.5),
                        clabel=trim.velocity.attrs['units'],
                        **map_settings
                    )

# All together now 🎹🎻🪕🥁

In [62]:
mapview + velocity_vert_profile + sand_conc_vert_profile * silt_conc_vert_profile + excess_density_vert_profile

:Layout
   .DynamicMap.I    :DynamicMap   [time]
      :Image   [XZ,YZ]   (velocity)
   .DynamicMap.II   :DynamicMap   [time,N]
      :NdOverlay   [N_KMAXOUT_RESTR]
         :Curve   [velocity]   (depth_center)
   .DynamicMap.Sand :DynamicMap   [time,N]
      :Overlay
         .NdOverlay.Sand :NdOverlay   [N_KMAXOUT_RESTR]
            :Curve   [R1]   (depth_center)
         .NdOverlay.Silt :NdOverlay   [N_KMAXOUT_RESTR]
            :Curve   [R1]   (depth_center)
   .DynamicMap.III  :DynamicMap   [time,N]
      :NdOverlay   [N_KMAXOUT_RESTR]
         :Curve   [delta_rho]   (depth_center)